# Dimensionality Reduction

One of the main difficulties in today’s environment is being able to visualize data easily. There is too much information, too much news, and too much data. Dimensionality is the number of dimensions, features or input variables associated in a dataset and dimensionality reduction means reducing the number of features in a dataset.

**Dimensionality reduction algorithms** project high-dimensional data to a low-dimensional space while retaining as much of the variation as possible. There are two main approaches to dimensionality reduction.

- The first one is known as linear projection which involves linearly projecting data from a high-dimensional space to a low-dimensional space. This includes techniques such as principal component analysis (PCA).
- The second approach is known as manifold learning which is also referred to as nonlinear dimensionality reduction. This includes techniques such as Uniform manifold approximation and projection (UMAP).

Dimensionality reduction techniques help to address the curse of dimensionality.

# Principal Component

PCA is a linear dimensionality reduction techniqu where the algorithm finds a low-dimensional representation of the data while retaining as much of the variation as possible and help reduce the complexity.

The main concept behind the PCA is to consider the correlation among features. If the correlation is very high among a subset of the features, **PCA will attempt to combine the highly correlated features and represent this data with a smaller number of linearly uncorrelated features**. The algorithm keeps performing this correlation reduction, finding the directions of maximum variance in the original high-dimensional data and projecting them onto a smaller dimensional space. These newly derived components are known as principal components.

Investors often refer to movements in the yield curve in terms of three driving factors:

- Level
- Slope
- Curvature

PCA formalizes this viewpoint and allows us to evaluate when a segment of the yield curve has cheapened or richened beyond that prescribed by recent yield movements. The essence of PCA in the context of rates market is that most yield curve movements can be represented as a set of two to three independent driving factors – the principal components (PCs) – along with their relative weightings. And, with these components, it is possible to reconstruct the original features.

We'll apply PCA to the set of yield curves fitted using the HJM model as discussed during the lecture. The PCs are ordered so that the first PC is the most important in capturing variability in the yield curves, the second PC is next most important, and so on.

The most intuitive way of obtaining PCs is via eigenvalue decomposition of a covariance matrix. The covariance measures the central tendency and talks about deviation from the mean. Intuitively, PCs represent ways in which the forward rates making up a yield curve can deviate from their mean levels.



In [1]:
# Import libraries
import numpy as np
import pandas as pd

# Plot settings
import cufflinks as cf
cf.set_config_file(offline=True)

# scikit
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA

pd.set_option('display.max_rows', 5000)
pd.set_option('display.max_columns', 100)
pd.set_option('display.width', 1000)

In [2]:
data = pd.read_csv('./data/BLG daily 2002 to 2007 hjm-lecture.txt', index_col=0, sep ='\t')

In [3]:
data.head()

0.08   0.5   1.0   1.5   2.0   2.5   3.0   3.5   4.0   4.5   5.0   5.5   6.0   6.5   7.0   7.5   8.0   8.5   9.0   9.5  10.0  10.5  11.0  11.5  12.0  12.5  13.0  13.5  14.0  14.5  15.0  15.5  16.0  16.5  17.0  17.5  18.0  18.5  19.0  19.5  20.0  20.5  21.0  21.5  22.0  22.5  23.0  23.5  24.0  24.5  25.0
1  5.77  6.44  6.71  6.65  6.50  6.33  6.15  5.99  5.84  5.71  5.57  5.44  5.30  5.16  5.01  4.86  4.71  4.55  4.39  4.24  4.09  3.94  3.81  3.68  3.57  3.46  3.37  3.29  3.23  3.18  3.15  3.13  3.12  3.12  3.13  3.16  3.19  3.22  3.27  3.31  3.36  3.42  3.48  3.54  3.60  3.66  3.73  3.79  3.86  3.92  3.99
2  5.77  6.45  6.75  6.68  6.54  6.39  6.23  6.08  5.95  5.82  5.69  5.56  5.43  5.28  5.13  4.97  4.80  4.63  4.46  4.29  4.13  3.97  3.82  3.68  3.55  3.44  3.33  3.25  3.18  3.12  3.08  3.06  3.05  3.05  3.06  3.09  3.12  3.16  3.21  3.26  3.32  3.38  3.44  3.51  3.58  3.65  3.72  3.80  3.87  3.95  4.02
3  5.78  6.44  6.74  6.68  6.56  6.41  6.26  6.12  5.98  5.84  5.71  5.57  5.43  5.28  5.12  4.96  4.79  4.62  4.45  4.28  4.11  3.95  3.80  3.66  3.53  3.41  3.31  3.22  3.14  3.08  3.04  3.01  2.99  2.99  3.00  3.02  3.04  3.08  3.12  3.16  3.22  3.27  3.33  3.39  3.45  3.52  3.59  3.65  3.72  3.79  3.86
4  5.74  6.41  6.69  6.62  6.49  6.35  6.20  6.06  5.93  5.79  5.66  5.52  5.38  5.23  5.07  4.91  4.74  4.57  4.40  4.23  4.06  3.91  3.75  3.61  3.48  3.36  3.25  3.15  3.07  3.01  2.96  2.92  2.90  2.89  2.89  2.90  2.92  2.95  2.99  3.03  3.08  3.13  3.19  3.25  3.31  3.37  3.44  3.51  3.58  3.65  3.72
5  5.74  6.40  6.64  6.55  6.42  6.27  6.13  5.98  5.85  5.72  5.58  5.44  5.30  5.15  5.00  4.83  4.67  4.50  4.33  4.17  4.00  3.85  3.70  3.56  3.42  3.30  3.19  3.09  3.01  2.94  2.89  2.85  2.82  2.80  2.80  2.80  2.82  2.84  2.88  2.92  2.96  3.01  3.07  3.12  3.19  3.25  3.32  3.38  3.45  3.53  3.60

In [4]:
data.shape

(1264, 51)

Representation of a yield curve as 50 forward rates. As the yield curve evolves over time, each forward rate can change. It is understood that adjacent points on the yield curve do not move independently. PCA is a method for identifying the dominant ways in which various points on the yield curve move together.

PCA allows us to take a set of yield curves, process them using standard mathematical methods, and then define a reduced form model for the yield curve. This reduced form model retains only a small number of principal components (PCs) but can reproduce the vast majority of yield curves that the full structural model could. This reduced model has fewer sources of uncertainty (i.e. dimensions) than if the 50 points of the yield curve were modelled independently.

In [5]:
# Plot curve
data.iloc[0].iplot(title = 'Representation of a Yield Curve')

In [6]:
# Plot all curves
data.iloc[:,].T.iplot(title='Daily Yield Curves')

We'll now produce the volatility chart by taking the first difference (scaling) and calculating historical variance by each individual maturity.

In [7]:
diff_ = data.diff(-1)
diff_.dropna(inplace=True)
diff_.tail()

0.08   0.5   1.0   1.5   2.0   2.5   3.0   3.5   4.0   4.5   5.0   5.5   6.0   6.5   7.0   7.5   8.0   8.5   9.0   9.5  10.0  10.5  11.0  11.5  12.0  12.5  13.0  13.5  14.0  14.5  15.0  15.5  16.0  16.5  17.0  17.5  18.0  18.5  19.0  19.5  20.0  20.5  21.0  21.5  22.0  22.5  23.0  23.5  24.0  24.5  25.0
1259  0.00  0.03  0.04  0.03  0.02  0.02  0.01  0.01  0.00  0.00  0.00  0.00 -0.01  0.00 -0.01  0.00  0.00  0.00  0.00  0.00  0.00 -0.01  0.00  0.00 -0.01  0.00  0.00  0.00 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01 -0.02 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01  0.00 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01 -0.01
1260  0.02  0.01  0.00  0.00  0.00 -0.01 -0.01 -0.01  0.00 -0.01 -0.01 -0.01  0.00  0.00  0.00 -0.01 -0.01 -0.01 -0.01  0.00 -0.01  0.00  0.00  0.00  0.00 -0.01 -0.01 -0.01  0.00  0.00 -0.01  0.00 -0.01  0.00 -0.01  0.00  0.00 -0.01 -0.01 -0.01 -0.01  0.00  0.00 -0.01 -0.01  0.00  0.00  0.00  0.00  0.00  0.00
1261 -0.01 -0.03 -0.08 -0.12 -0.13 -0.13 -0.13 -0.13 -0.14 -0.13 -0.14 -0.14 -0.14 -0.14 -0.14 -0.14 -0.13 -0.14 -0.13 -0.14 -0.13 -0.13 -0.13 -0.13 -0.12 -0.11 -0.11 -0.11 -0.11 -0.11 -0.10 -0.10 -0.10 -0.10 -0.10 -0.10 -0.10 -0.10 -0.09 -0.09 -0.09 -0.10 -0.10 -0.10 -0.09 -0.10 -0.10 -0.10 -0.10 -0.10 -0.10
1262  0.00  0.00  0.01  0.02  0.01  0.01  0.01  0.00  0.01  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.01  0.01  0.01  0.01  0.01  0.01  0.01  0.01  0.01  0.01  0.02  0.01  0.01  0.02  0.01  0.02  0.01  0.02  0.02  0.01  0.01  0.01  0.02  0.01  0.02  0.01  0.01  0.01  0.01  0.01  0.01  0.00
1263  0.02  0.00  0.03  0.03  0.04  0.04  0.05  0.06  0.06  0.06  0.07  0.07  0.06  0.05  0.05  0.05  0.04  0.04  0.03  0.02  0.02  0.02  0.02  0.02  0.02  0.02  0.02  0.03  0.02  0.02  0.03  0.03  0.03  0.04  0.04  0.04  0.04  0.04  0.04  0.05  0.05  0.04  0.05  0.04  0.05  0.05  0.05  0.05  0.05  0.05  0.06

In [8]:
diff_.shape

(1263, 51)

## Derive Volatility
The drift of forward rate is fully determined by volatility of forward rate dynamics.

In [9]:
vol = np.std(diff_, axis=0) * 10000

In [10]:
vol[:].iplot(title='Volatility of daily UK government yields', xTitle='Tenor', yTitle='Volatility (bps)',
         color='cornflowerblue')

The above volatility plot is of the averaged values, but we can see that different parts of the yield curve move differently. As you can see volatility is very significant, especially at the shorter end of the curve. This means that 1-year and 2-year rates seems to move up and down a lot as compared to other tenors.

It is never all up or all down and PCA help us figure out exactly what is going. Covariance of daily changes shows dependency of different rates. Principal components can be calculated by finding the eigenvalues and eigenvectors of this covariance matrix of below.

PCA decomposes the volatility.

## Calculate Covariance

In [11]:
cov_= pd.DataFrame(np.cov(diff_, rowvar=False)*252/10000, columns=diff_.columns, index=diff_.columns)
cov_.style.format("{:.4%}")

## Eigen Decomposition

In [12]:
# Perform eigen decomposition
eigenvalues, eigenvectors = np.linalg.eig(cov_)

# Sort values (good practice)
idx = eigenvalues.argsort()[::-1]   
eigenvalues = eigenvalues[idx]
eigenvectors = eigenvectors[:,idx]

# Format into a DataFrame 
df_eigval = pd.DataFrame({"Eigenvalues": eigenvalues})

eigenvalues

array([2.02898049e-03, 4.63398406e-04, 1.63446845e-04, 8.51547101e-05,
       5.10538526e-05, 3.32765289e-05, 1.58231855e-05, 4.49832087e-06,
       1.94407432e-06, 8.99455051e-07, 6.04790270e-07, 5.90792253e-07,
       5.89198637e-07, 5.57023543e-07, 5.55577838e-07, 5.37017622e-07,
       5.25225242e-07, 5.09484922e-07, 5.02130032e-07, 4.95037888e-07,
       4.85536393e-07, 4.74757652e-07, 4.66830631e-07, 4.56358980e-07,
       4.53910470e-07, 4.45678829e-07, 4.35704316e-07, 4.34084479e-07,
       4.26484963e-07, 4.13347804e-07, 4.01916308e-07, 3.97702101e-07,
       3.90292851e-07, 3.86498129e-07, 3.76760528e-07, 3.73179456e-07,
       3.63351112e-07, 3.57997757e-07, 3.48773694e-07, 3.42142905e-07,
       3.35540502e-07, 3.27434287e-07, 3.20549997e-07, 3.13802097e-07,
       3.06870950e-07, 3.04664148e-07, 2.99586146e-07, 2.88553566e-07,
       2.83944056e-07, 2.67537628e-07, 2.48780504e-07])

## Explained Variance

In [13]:
# Work out explained proportion 
df_eigval["Explained proportion"] = df_eigval["Eigenvalues"] / np.sum(df_eigval["Eigenvalues"])
df_eigval = df_eigval[:10]

#Format as percentage
df_eigval.style.format({"Explained proportion": "{:.2%}"})

In [14]:
(df_eigval['Explained proportion'][:10]*100).iplot(kind='bar', 
                                             title='Percentage of overall variance explained', 
                                             color='cornflowerblue')

## Visualize PCs

In [15]:
# Subsume first 3 components into a dataframe
pcadf = pd.DataFrame(eigenvectors[:,0:3], columns=['PC1','PC2','PC3'])
pcadf

PC1       PC2       PC3
0   0.004091 -0.008275  0.000235
1   0.056204 -0.161934 -0.271539
2   0.101034 -0.239236 -0.401805
3   0.116817 -0.243675 -0.357226
4   0.121388 -0.235475 -0.275176
5   0.125890 -0.226757 -0.195816
6   0.129107 -0.219537 -0.123907
7   0.133088 -0.211509 -0.062428
8   0.136317 -0.204675 -0.007698
9   0.139725 -0.197136  0.041132
10  0.143437 -0.191181  0.083977
11  0.145949 -0.180393  0.118443
12  0.148748 -0.172138  0.148917
13  0.150411 -0.160388  0.168783
14  0.152368 -0.148221  0.187009
15  0.153760 -0.132153  0.194324
16  0.153588 -0.116328  0.198019
17  0.153564 -0.099369  0.198828
18  0.152656 -0.079885  0.190827
19  0.152758 -0.060762  0.181945
20  0.151465 -0.040957  0.166998
21  0.150211 -0.019146  0.153529
22  0.149769  0.002883  0.136339
23  0.147382  0.024786  0.113789
24  0.147218  0.045120  0.093919
25  0.145850  0.062521  0.073232
26  0.145235  0.080535  0.057018
27  0.144742  0.095643  0.034725
28  0.143955  0.109272  0.019208
29  0.143280  0.121865  0.002660
30  0.142915  0.131281 -0.009064
31  0.142552  0.139612 -0.025011
32  0.141971  0.146575 -0.036411
33  0.142739  0.148606 -0.047650
34  0.141743  0.151356 -0.057869
35  0.142540  0.152558 -0.065771
36  0.142059  0.152285 -0.069299
37  0.142475  0.149614 -0.076175
38  0.142345  0.147428 -0.078466
39  0.142238  0.142025 -0.083315
40  0.141697  0.136366 -0.086055
41  0.141526  0.130410 -0.085717
42  0.143090  0.123811 -0.088340
43  0.142231  0.117466 -0.083750
44  0.142732  0.108394 -0.087111
45  0.142453  0.100238 -0.083129
46  0.142918  0.091938 -0.082477
47  0.143170  0.082600 -0.076814
48  0.142951  0.073722 -0.074059
49  0.143502  0.064159 -0.071189
50  0.143605  0.053235 -0.066187

In [16]:
pcadf.iplot(title='First Three Principal Components', secondary_y='PC1', secondary_y_title='PC1', 
            yTitle='change in yield (bps)')

One of the key interpretations of PCA as applied to interest rates are the components of the yield curve. We can attribute the first three principal components to

- PC1: Parallel shifts in yield curve (shifts across the entire yield curve)
- PC2: Changes in short/long rates (steepening/flattening of the curve)
- PC3: Changes in curvature of the model (twists)

The **first PC** represents the situation that all forward rates in the yield curve move in the same direction but points around the 15 year term move more than points at the shorter or longer parts of the yield curve. This corresponds to a general rise (or fall) of all of the forward rates in the yield curve, but cannot be called a uniform or parallel shift. The impact of the first PC can be easily observed amongst the yield curves as it contributes more than 71% of the variability.

The **second PC** represents situations in which the short end of the yield curve moves up at the same time as the long end moves down, or vice versa. This is often described as a tilt in the yield curve, although in practice there is more subtle definition to the shape. This reflects the particular yield curves that were used for the analysis, as well as the structural model and calibration that were used to create them. In this example, the influence of the second PC accounts for about 16.27% of the variability in the yield curves.

The **third PC** is further interpreted as a higher order buckling in which the short end and long end move up at the same time as a region of medium term rates move down, or vice versa. In this particular example, this type of movement is only responsible for about 5.75% of the variability.

Having identified the most important factors, we can use their functional form to predict the most likely evolution of the yeild curve. Thus, a simple linear regression is fitted for the shift factor as it simply moves the curve up and down. Second degree polynomial is fitted for the tilt factor and higher degree can approximate flexing. 

Thus, yield curve can be approximated by linear combination of first three loadings.

---

# UK Government Bond Rates

The purpose of applying PCA to financial markets is to explain the price changes of different assets through a smaller set of factors. This is achieved via the dimensionality reduction of the observations where we pick meaningful factors (among many) explaining the most of the price changes. We'll now apply the principal component analysis to UK government bond spot rates from 0.5 years up to 10 years to maturity.

We'll adopt how two methods to decompose the yield curve: 
- one using eigen decomposition as we above, and 
- another by applying direct functions from scikit-learn.

## Method 1: Eigen Decomposition

In [17]:
# Import Bank of England spot curve data from excel
df = pd.read_excel("./data/GLC monthly_1970 to 2015.xlsx", 
                   index_col=0, header=3, sheet_name="4. spot curve", skiprows=[4])

# Select all of the data up to 10 years
df = df.iloc[:,0:20]

df.head()

0.5         1       1.5         2       2.5         3       3.5         4       4.5         5       5.5         6       6.5         7       7.5         8       8.5         9       9.5        10
years:                                                                                                                                                                                                       
1970-01-31  NaN  8.635354  8.707430  8.700727  8.664049  8.618702  8.572477  8.528372  8.487617  8.450611  8.417442  8.388098  8.362503  8.340549  8.322116  8.307105  8.295429  8.287013  8.281788  8.279691
1970-02-28  NaN  8.413131  8.397269  8.370748  8.337633  8.301590  8.265403  8.230804  8.198713  8.169617  8.143742  8.121153  8.101810  8.085616  8.072457  8.062236  8.054864  8.050261  8.048354  8.049074
1970-03-31  NaN  7.744187  7.782761  7.795017  7.793104  7.784963  7.775288  7.766459  7.759564  7.755068  7.753158  7.753877  7.757181  7.762973  7.771153  7.781635  7.794347  7.809221  7.826197  7.845220
1970-04-30  NaN  7.606512  7.864352  7.973522  8.002442  7.992813  7.967524  7.938335  7.911422  7.890054  7.875751  7.868985  7.869583  7.877024  7.890789  7.910452  7.935656  7.966093  8.001490  8.041602
1970-05-31  NaN  7.391107  7.735838  7.862182  7.877510  7.840673  7.782249  7.718053  7.656856  7.603548  7.560502  7.528577  7.507706  7.497355  7.496983  7.506125  7.524371  7.551351  7.586723  7.630168

In [18]:
# Drop nan values
df = df.dropna(how="any")
df.shape

(456, 20)

In [19]:
# Standarized data
scaler = StandardScaler()
scaler.fit(df)

df_std = pd.DataFrame(scaler.transform(df), columns=df.columns)
df_std.head()

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.



0.5         1       1.5         2       2.5         3       3.5         4       4.5         5       5.5         6       6.5         7       7.5         8       8.5         9       9.5        10
0  0.046393  0.137629  0.114852  0.075536  0.040097  0.011058 -0.011958 -0.029713 -0.042998 -0.052439 -0.058488 -0.061490 -0.061729 -0.059439 -0.054804 -0.047976 -0.039083 -0.028242 -0.015559 -0.001132
1  0.052706  0.089935  0.084148  0.064262  0.042095  0.021662  0.004165 -0.010140 -0.021293 -0.029374 -0.034487 -0.036762 -0.036346 -0.033381 -0.027985 -0.020263 -0.010314  0.001770  0.015895  0.031971
2  0.070345  0.094904  0.076732  0.052266  0.029015  0.008896 -0.007742 -0.021056 -0.031301 -0.038689 -0.043398 -0.045580 -0.045381 -0.042921 -0.038304 -0.031620 -0.022956 -0.012395 -0.000020  0.014088
3  0.107418  0.167307  0.168964  0.144128  0.112896  0.082938  0.056761  0.035002  0.017677  0.004656 -0.004286 -0.009443 -0.011134 -0.009634 -0.005157  0.002113  0.012016  0.024407  0.039151  0.056119
4  0.066680  0.069013  0.061107  0.056853  0.057613  0.062163  0.069256  0.077907  0.087515  0.097789  0.108622  0.120026  0.132059  0.144771  0.158200  0.172368  0.187283  0.202943  0.219334  0.236436

In [20]:
# Create a covariance matrix 
cov_matrix_array = np.cov(df_std, rowvar=False)
pd.DataFrame(cov_matrix_array, columns=df.columns , index =df.columns ) #, index=range(1,21), columns=range(1,21))

0.5         1       1.5         2       2.5         3       3.5         4       4.5         5       5.5         6       6.5         7       7.5         8       8.5         9       9.5        10
0.5  1.002198  0.998543  0.992527  0.986072  0.979831  0.973998  0.968590  0.963540  0.958753  0.954135  0.949610  0.945122  0.940638  0.936137  0.931605  0.927030  0.922406  0.917724  0.912977  0.908156
1    0.998543  1.002198  1.000387  0.996565  0.992087  0.987522  0.983078  0.978799  0.974651  0.970581  0.966533  0.962470  0.958369  0.954214  0.949998  0.945715  0.941361  0.936932  0.932423  0.927829
1.5  0.992527  1.000387  1.002198  1.001082  0.998610  0.995567  0.992311  0.988984  0.985621  0.982212  0.978739  0.975185  0.971542  0.967809  0.963986  0.960075  0.956077  0.951991  0.947816  0.943548
2    0.986072  0.996565  1.001082  1.002198  1.001480  0.999820  0.997672  0.995249  0.992637  0.989867  0.986948  0.983885  0.980687  0.977362  0.973920  0.970370  0.966718  0.962967  0.959119  0.955170
2.5  0.979831  0.992087  0.998610  1.001480  1.002198  1.001708  1.000521  0.998899  0.996966  0.994781  0.992377  0.989774  0.986993  0.984054  0.980972  0.977763  0.974436  0.970999  0.967455  0.963803
3    0.973998  0.987522  0.995567  0.999820  1.001708  1.002198  1.001839  1.000924  0.999604  0.997959  0.996036  0.993869  0.991487  0.988917  0.986181  0.983298  0.980282  0.977142  0.973884  0.970509
3.5  0.968590  0.983078  0.992311  0.997672  1.000521  1.001839  1.002198  1.001913  1.001154  1.000013  0.998547  0.996800  0.994805  0.992596  0.990197  0.987632  0.984917  0.982064  0.979080  0.975969
4    0.963540  0.978799  0.988984  0.995249  0.998899  1.000924  1.001913  1.002198  1.001957  1.001291  1.000264  0.998924  0.997310  0.995455  0.993389  0.991138  0.988720  0.986148  0.983432  0.980576
4.5  0.958753  0.974651  0.985621  0.992637  0.996966  0.999604  1.001154  1.001957  1.002198  1.001983  1.001380  1.000437  0.999196  0.997692  0.995957  0.994018  0.991894  0.989601  0.987149  0.984544
5    0.954135  0.970581  0.982212  0.989867  0.994781  0.997959  1.000013  1.001291  1.001983  1.002198  1.002002  1.001446  1.000571  0.999414  0.998007  0.996377  0.994546  0.992530  0.990341  0.987986
5.5  0.949610  0.966533  0.978739  0.986948  0.992377  0.996036  0.998547  1.000264  1.001380  1.002002  1.002198  1.002017  1.001500  1.000684  0.999601  0.998278  0.996739  0.994999  0.993072  0.990965
6    0.945122  0.962470  0.975185  0.983885  0.989774  0.993869  0.996800  0.998924  1.000437  1.001446  1.002017  1.002198  1.002029  1.001547  1.000783  0.999764  0.998513  0.997049  0.995384  0.993526
6.5  0.940638  0.958369  0.971542  0.980687  0.986993  0.991487  0.994805  0.997310  0.999196  1.000571  1.001500  1.002029  1.002198  1.002040  1.001588  1.000868  0.999904  0.998713  0.997309  0.995701
7    0.936137  0.954214  0.967809  0.977362  0.984054  0.988917  0.992596  0.995455  0.997692  0.999414  1.000684  1.001547  1.002040  1.002198  1.002050  1.001623  1.000941  1.000021  0.998877  0.997519
7.5  0.931605  0.949998  0.963986  0.973920  0.980972  0.986181  0.990197  0.993389  0.995957  0.998007  0.999601  1.000783  1.001588  1.002050  1.002198  1.002058  1.001653  1.001001  1.000116  0.999007
8    0.927030  0.945715  0.960075  0.970370  0.977763  0.983298  0.987632  0.991138  0.994018  0.996377  0.998278  0.999764  1.000868  1.001623  1.002058  1.002198  1.002065  1.001677  1.001048  1.000188
8.5  0.922406  0.941361  0.956077  0.966718  0.974436  0.980282  0.984917  0.988720  0.991894  0.994546  0.996739  0.998513  0.999904  1.000941  1.001653  1.002065  1.002198  1.002070  1.001695  1.001083
9    0.917724  0.936932  0.951991  0.962967  0.970999  0.977142  0.982064  0.986148  0.989601  0.992530  0.994999  0.997049  0.998713  1.000021  1.001001  1.001677  1.002070  1.002198  1.002074  1.001708
9.5  0.912977  0.932423  0.947816  0.959119  0.967455  0.973884  0.979080  0.983432  0.987149  0.990341  0.993072  0.995384  0.997309 

## Eigen Decompose

In [21]:
# Perform eigen decomposition

eigenvalues, eigenvectors = np.linalg.eig(cov_matrix_array)

# Sort values (good practice)
idx = eigenvalues.argsort()[::-1]   
eigenvalues = eigenvalues[idx]
eigenvectors = eigenvectors[:,idx]

# Format into a DataFrame 
df_eigval = pd.DataFrame({"Eigenvalues": eigenvalues}) #, index=range(1,21))

pd.DataFrame(eigenvalues, columns=['Eigenvalue'])

Eigenvalue
0   1.970405e+01
1   3.105335e-01
2   2.494456e-02
3   3.504700e-03
4   8.073795e-04
5   1.029768e-04
6   8.617937e-06
7   1.211792e-06
8   9.369179e-08
9   1.491070e-08
10  2.841015e-09
11  5.914032e-10
12  1.353173e-10
13  3.395947e-11
14  7.775703e-12
15  2.564338e-12
16  1.119944e-12
17  2.914111e-13
18  6.641689e-14
19  1.041060e-14

In [22]:
# Format into a DataFrame 
df_eigvec = pd.DataFrame(eigenvectors) #, index=range(1,21))

pd.DataFrame(eigenvectors[:,0], columns=['The Vector of the 1st Princial Component'])

The Vector of the 1st Princial Component
0                                   0.216371
1                                   0.219680
2                                   0.221913
3                                   0.223323
4                                   0.224190
5                                   0.224729
6                                   0.225064
7                                   0.225263
8                                   0.225360
9                                   0.225372
10                                  0.225309
11                                  0.225177
12                                  0.224983
13                                  0.224732
14                                  0.224429
15                                  0.224077
16                                  0.223682
17                                  0.223245
18                                  0.222769
19                                  0.222255

In [23]:
# Work out explained proportion 
df_eigval["Explained proportion"] = df_eigval["Eigenvalues"] / np.sum(df_eigval["Eigenvalues"])

#Format as percentage
df_eigval.style.format({"Explained proportion": "{:.2%}"})

In [24]:
(df_eigval['Explained proportion'][:10]*100).iplot(kind='bar', 
                                             title='Percentage of overall variance explained', 
                                             color='cornflowerblue')

In [25]:
# Subsume first 3 components into a dataframe
pcdf = pd.DataFrame(eigenvectors[:,0:3], columns=['PC1','PC2','PC3'])
pcdf

PC1       PC2       PC3
0   0.216371 -0.476742  0.568237
1   0.219680 -0.398921  0.244808
2   0.221913 -0.317188  0.019318
3   0.223323 -0.245476 -0.124801
4   0.224190 -0.184527 -0.209822
5   0.224729 -0.131987 -0.253173
6   0.225064 -0.085706 -0.266431
7   0.225263 -0.044103 -0.257638
8   0.225360 -0.006087 -0.232802
9   0.225372  0.029085 -0.196639
10  0.225309  0.061930 -0.152829
11  0.225177  0.092806 -0.104154
12  0.224983  0.121967 -0.052702
13  0.224732  0.149614 -0.000065
14  0.224429  0.175910  0.052549
15  0.224077  0.200994  0.104255
16  0.223682  0.224988  0.154429
17  0.223245  0.247999  0.202659
18  0.222769  0.270118  0.248692
19  0.222255  0.291427  0.292403

In [26]:
pcdf.iplot(title='First Three Principal Components', secondary_y='PC1', secondary_y_title='PC1')

# PCA Decomposition using Sklearn

In [27]:
# Scale and fit the model
pipe = Pipeline([("scaler", StandardScaler()), ("pca", PCA())]) 
pipe.fit(df)

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.



Pipeline(steps=[('scaler', StandardScaler()), ('pca', PCA())])

In [28]:
# eigenvectors
pipe['pca'].components_[0]

array([0.2163711 , 0.21967968, 0.22191335, 0.2233227 , 0.22419027,
       0.22472894, 0.22506385, 0.22526262, 0.22535956, 0.2253718 ,
       0.22530883, 0.22517738, 0.2249833 , 0.22473203, 0.22442859,
       0.2240774 , 0.22368207, 0.22324536, 0.22276915, 0.22225453])

In [29]:
# eigen values
pipe['pca'].explained_variance_

array([1.97040530e+01, 3.10533489e-01, 2.49445560e-02, 3.50469991e-03,
       8.07379451e-04, 1.02976761e-04, 8.61793663e-06, 1.21179203e-06,
       9.36917912e-08, 1.49106974e-08, 2.84101504e-09, 5.91403577e-10,
       1.35317277e-10, 3.39584209e-11, 7.77565136e-12, 2.56435621e-12,
       1.12010259e-12, 2.91862679e-13, 6.62857318e-14, 1.05315377e-14])

In [30]:
# eigen values proportion
pipe['pca'].explained_variance_ratio_

array([9.83042118e-01, 1.54926247e-02, 1.24449265e-03, 1.74850708e-04,
       4.02804441e-05, 5.13754673e-06, 4.29951882e-07, 6.04567298e-08,
       4.67431634e-09, 7.43899926e-10, 1.41739237e-10, 2.95053319e-11,
       6.75102643e-12, 1.69419753e-12, 3.87929975e-13, 1.27936631e-13,
       5.58823112e-14, 1.45611315e-14, 3.30701842e-15, 5.25422109e-16])

In [31]:
df2 = pd.DataFrame({'Eigenvalues': pipe['pca'].explained_variance_,
                    'Explained proportion': pipe['pca'].explained_variance_ratio_})
#Format as percentage
df2.style.format({"Explained proportion": "{:.2%}"})

# PCA Projections

In [32]:
# Standarized data
scaler = StandardScaler()
scaler.fit(df)

df_std = pd.DataFrame(scaler.transform(df), columns=df.columns)
df_std.head()

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.

/Users/mie/opt/anaconda3/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning:

Feature names only support names that are all strings. Got feature names with dtypes: ['float', 'int']. An error will be raised in 1.2.



0.5         1       1.5         2       2.5         3       3.5         4       4.5         5       5.5         6       6.5         7       7.5         8       8.5         9       9.5        10
0  0.046393  0.137629  0.114852  0.075536  0.040097  0.011058 -0.011958 -0.029713 -0.042998 -0.052439 -0.058488 -0.061490 -0.061729 -0.059439 -0.054804 -0.047976 -0.039083 -0.028242 -0.015559 -0.001132
1  0.052706  0.089935  0.084148  0.064262  0.042095  0.021662  0.004165 -0.010140 -0.021293 -0.029374 -0.034487 -0.036762 -0.036346 -0.033381 -0.027985 -0.020263 -0.010314  0.001770  0.015895  0.031971
2  0.070345  0.094904  0.076732  0.052266  0.029015  0.008896 -0.007742 -0.021056 -0.031301 -0.038689 -0.043398 -0.045580 -0.045381 -0.042921 -0.038304 -0.031620 -0.022956 -0.012395 -0.000020  0.014088
3  0.107418  0.167307  0.168964  0.144128  0.112896  0.082938  0.056761  0.035002  0.017677  0.004656 -0.004286 -0.009443 -0.011134 -0.009634 -0.005157  0.002113  0.012016  0.024407  0.039151  0.056119
4  0.066680  0.069013  0.061107  0.056853  0.057613  0.062163  0.069256  0.077907  0.087515  0.097789  0.108622  0.120026  0.132059  0.144771  0.158200  0.172368  0.187283  0.202943  0.219334  0.236436

In [33]:
# Calculate principal components
principal_components = df_std.dot(eigenvectors)
principal_components.index = df.index
principal_components.head()

0         1         2         3         4         5         6         7         8         9         10        11            12        13            14            15            16            17            18            19
years:                                                                                                                                                                                                                                        
1970-07-31 -0.032874 -0.205143  0.067556 -0.146754 -0.004555 -0.021764 -0.001972  0.000829 -0.000340  0.000109  0.000050 -0.000001 -2.264623e-07 -0.000005  1.986361e-06  1.982405e-06  7.113005e-08 -2.241215e-07  2.360908e-07  9.386371e-09
1970-08-31  0.031912 -0.126972  0.062992 -0.105436 -0.031698 -0.008191 -0.003187  0.001165 -0.000124 -0.000057  0.000017 -0.000001  3.762067e-06 -0.000003 -2.017369e-07  2.319194e-06 -5.037226e-08 -1.518963e-07  2.483496e-07 -1.159396e-08
1970-09-30 -0.009340 -0.150541  0.078729 -0.089413 -0.024909 -0.010715 -0.002032  0.001371 -0.000030 -0.000024  0.000017 -0.000004  7.756489e-06 -0.000002 -7.401496e-07  1.257886e-06 -1.558535e-07  1.031069e-07  1.472247e-07 -3.079493e-08
1970-10-31  0.220205 -0.213823  0.048540 -0.144961 -0.037556 -0.004846 -0.004420  0.001127 -0.000176 -0.000110 -0.000008 -0.000014  8.061238e-06 -0.000006 -4.119794e-07  2.863548e-06 -7.676475e-07  5.692306e-08  1.920244e-07 -3.847324e-08
1971-01-31  0.534111  0.220168  0.126862 -0.031169 -0.011036 -0.010601 -0.002910  0.000232  0.000051 -0.000002  0.000012  0.000010  8.802472e-06  0.000004 -3.545191e-07  3.576012e-07 -1.369722e-07  6.249949e-08  5.894576e-08 -4.817906e-09

In [34]:
principal_components.shape

(456, 20)

### PC1: Yield

In [35]:
level = pd.DataFrame({'10Y': df[10.0],
                      'PC1': principal_components[0]})
level.head()

10Y       PC1
years:                        
1970-07-31  7.559915 -0.032874
1970-08-31  7.678102  0.031912
1970-09-30  7.614256 -0.009340
1970-10-31  7.764320  0.220205
1971-01-31  8.408105  0.534111

In [36]:
level.iplot(title='PC1 : Yield', secondary_y='PC1')

### PC2: Slope

In [37]:
# Calculate 10Y-2M slope
slope = pd.DataFrame(df)
slope = slope[[2,10]] # 2-year & 10-year
# slope here is considered as the difference between long-run rate minus short-run rate
slope['slope'] = slope[10] - slope[2]
slope['PC2'] = principal_components[1]
slope.head()

2        10     slope       PC2
years:                                            
1970-07-31  7.106046  7.559915  0.453869 -0.205143
1970-08-31  7.063535  7.678102  0.614567 -0.126972
1970-09-30  7.018305  7.614256  0.595951 -0.150541
1970-10-31  7.364677  7.764320  0.399643 -0.213823
1971-01-31  7.035600  8.408105  1.372505  0.220168

In [38]:
slope[['slope', 'PC2']].iplot(title='PC2 : Slope', secondary_y='PC2')

In [39]:
# Verify the correlation
np.corrcoef(principal_components[1], slope['slope'])

array([[1.        , 0.95856134],
       [0.95856134, 1.        ]])

---

In [41]:
pd.DataFrame(np.c_[principal_components[[0]], df[10]], columns=['10Yr-Rate','Component']).iplot(title='One Component', secondary_y='Component')

In [42]:
pd.DataFrame(np.c_[ principal_components[[0,1]].sum(axis=1), df[10]], columns=['10Yr-Rate','Components']).iplot(title='Two Components', secondary_y='Components')

In [43]:
pd.DataFrame(np.c_[ principal_components[[0,1,2]].sum(axis=1), df[10]], columns=['10Yr-Rate','Components']).iplot(title='Three Components', secondary_y='Components')

Including more components would make the fitting more accurate.